In [11]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from scipy.sparse import hstack
import pandas as pd

In [2]:
# Load the dataset
file_path = 'sepsis_diab_pt_all.xlsx'  # Update if needed
# Load all sheets
sheets = pd.ExcelFile(file_path)
sheet_names = sheets.sheet_names
print("Available Sheets:", sheet_names)

Available Sheets: ['sepsis_pt_all_admission details', 'sepsis_lab_events', 'microbiology events', 'prescriptoin', 'poe', 'poe_detail']


In [3]:
# Load individual sheets
admission_data = sheets.parse('sepsis_pt_all_admission details')
lab_events = sheets.parse('sepsis_lab_events')
microbiology_events = sheets.parse('microbiology events')
prescription_data = sheets.parse('prescriptoin')
#poe_data = sheets.parse('poe')
#poe_details = sheets.parse('poe_detail')

In [4]:
admission_data.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2791 entries, 0 to 2790
Data columns (total 59 columns):
 #   Column                Non-Null Count  Dtype         
---  ------                --------------  -----         
 0   subject_id            2791 non-null   int64         
 1   hadm_id               2791 non-null   int64         
 2   admittime             2791 non-null   datetime64[ns]
 3   dischtime             2791 non-null   datetime64[ns]
 4   deathtime             158 non-null    datetime64[ns]
 5   admission_type        2791 non-null   object        
 6   admit_provider_id     2791 non-null   object        
 7   admission_location    2791 non-null   object        
 8   discharge_location    2777 non-null   object        
 9   insurance             2791 non-null   object        
 10  language              2791 non-null   object        
 11  marital_status        2736 non-null   object        
 12  race                  2791 non-null   object        
 13  edregtime         

In [5]:
# Select relevant columns
admission_data = admission_data[['hadm_id', 'admission_type', 'drg_code', 'dx_1_code', 'edhours']].drop_duplicates()
prescription_data = prescription_data[['hadm_id', 'drug']].drop_duplicates()

prescription_data=prescription_data.reset_index()

# Drop rows with missing values in critical columns
admission_data.dropna(subset=['hadm_id', 'admission_type', 'drg_code', 'dx_1_code', 'edhours'], inplace=True)
prescription_data.dropna(subset=['hadm_id', 'drug'], inplace=True)

# Merge admissions and prescriptions
admission_drug_data = pd.merge(prescription_data, admission_data, on='hadm_id', how='inner')

# Encode categorical variables
categorical_features = pd.get_dummies(
    admission_drug_data[['admission_type', 'drg_code', 'dx_1_code']],
    drop_first=True
)

# Scale numerical features (EDHOURS)
scaler = StandardScaler()
numerical_features = scaler.fit_transform(admission_drug_data[['edhours']])

numerical_features = pd.DataFrame(numerical_features, columns=['scaled_edhours'])

# TF-IDF for drug names
tfidf_vectorizer = TfidfVectorizer(stop_words='english')
drug_tfidf_matrix = tfidf_vectorizer.fit_transform(admission_drug_data['drug'])

# Combine All Features into a Single DataFrame
combined_features = pd.concat([categorical_features.reset_index(drop=True), numerical_features.reset_index(drop=True)], axis=1).reset_index(drop=True)

print("Combined Features Shape:", combined_features.shape)

Combined Features Shape: (50196, 210)


In [8]:
import pandas as pd

from ydata_profiling import ProfileReport

In [7]:
#pip install ydata-profiling

  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
   ---------------------------------------- 0.0/666.3 kB ? eta -:--:--
   ---------------------------------------- 666.3/666.3 kB 8.6 MB/s eta 0:00:00
   ---------------------------------------- 0.0/9.9 MB ? eta -:--:--
   -------- ------------------------------- 2.1/9.9 MB 11.8 MB/s eta 0:00:01
   --------------- ------------------------ 3.9/9.9 MB 10.2 MB/s eta 0:00:01
   ------------------------- -------------- 6.3/9.9 MB 10.7 MB/s eta 0:00:01
   ------------------------------ --------- 7.6/9.9 MB 9.8 MB/s eta 0:00:01
   ---------------------------------------  9.7/9.9 MB 9.7 MB/s eta 0:00:01
   ---------------------------------------- 9.9/9.9 MB 9.2 MB/s eta 0:00:00
   ---------------------------------------- 0.0/4.3 MB ? eta -:--:--
   ------------ --------------------------- 1.3/4.3 MB 6.1 MB/s eta 0:00:01
   ---------------------- ----------------- 2.4/4.3 MB 5.6 MB/s eta 0:00:0

  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


In [9]:
df=ProfileReport(combined_features, title="Trending Books")

In [10]:
df.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
#END